# MPAGS Spectroscopy assignment

Code by M. Borgi, modified by M. Lafarga Magro


In this assignment you are going to extract the long-slit spectra of two stars using DS9 and this python code. Below you have:
1. The instructions to open and draw regions in DS9
2. Some python code to read in the regions drawn with DS9 and extract the spectra
3. Some questions for you to answer

Please mail marina.lafarga-magro@warwick.ac.uk your answers by the end of the MPAGS course, but preferable before. Please make the header of the email "MPAGS 2023 spectroscopy [your name]". If you have any problems with the assignment let me know. Remember: there is no mark associated with the assignment, as the aim is that you engage with the topic. We will just keep note of whether you tried these questions.

## Questions

Here you have all the questions you should try to answer. These questions are repeated again below in their corresponding sections.

After opening the science image with DS9 (see below), try to answer the following questions:

1. How many sources do you see in the science image?

2. What are the spectral and the spatial directions?

3. How was the slit oriented with respect to the image coordinates?

After extracting the spectrum with the python code (again, see below), try to answer the following questions:

4. Plot the 1D extracted spectrum of the sources and the sky.

5. Look at the extracted sky spectra. Contrary to what we saw in the lecture, the sky emission lines are not clearly visible. The sky spectrum looks smooth and low-resolution. What does this tell you about the slit?

6. Look at the extracted spectrum of the two sources. Even without having performed any flux calibration, could you tell which one of the stars is hotter? Why?

7. Among the methods discussed for wavelength calibration, which one(s) would be applicable to these data?


## DS9 instructions

Open the science spectrum `science_spec.fits` with DS9. 

Try to answer the following questions:

1. How many sources do you see in the science image?

2. What are the spectral and the spatial directions?

3. How was the slit oriented with respect to the image coordinates?

We will now use DS9 to drag lines tracing the position of the spectral trails. These will be subsequently used to extract the 1D spectrum. Make sure `Edit` -> `Region` is selected from the scroll-down menu at the top, and adjust the zoom and color scaling parameters. Select `Region` -> `Shape` -> `Line` and draw a line on top of each spectral trace. Lines can be selected and moved / resized with one click. Double-clicking allows you to manually specify start and end points. When you are happy with the result, save the region file with `Region` -> `Save Regions`. In the pop-up window, make sure to select your current folder, and use `trails.reg` as file name. In the last pop-up window, select "DS9" as "Format" and "Physical" as "Coordinate System".

This should result in a file named `trails.reg` in the current directory. That's it for DS9, we will now continue in this notebook.


The following code will read in the trails you have just drawn, compute and remove the sky around each of the spectral trails, and extract the 1D spectra by co-adding the trails along the spatial dimension. After this, try plotting the extracted spectrum and answer the questions you will find below.

## Load libraries

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

## Load science data

Read in the science observation `science_spec.npy`. This is the same as the `science_spec.fits` but it is ready to be read in python.

In [ ]:
img = np.load('science_spec.npy')

ny = img.shape[0]       # Number of pixel along spectral direction
nx = img.shape[1]       # Number of pixel along spatial direction

We can have a look at the image here. This should result in something similar as what we saw in DS9.

In [ ]:
fig, ax = plt.subplots()
ax.imshow(img, vmax=6000)
ax.set_title('science_spec')
plt.tight_layout()
plt.show()

## Load trails from DS9 and reformat

Read in the region file you created with DS9 containing the trail positions `trails.reg` and reformat into pixel coordinates.

In [ ]:
# Read
with open('trails.reg','r') as f:
    flist = f.read()

# Reformat
nlines = 2  # Two sources
yy = np.zeros((nlines,2))
xx = np.zeros((nlines,2))

# Reformatting DS9 into pixel coordinates - skipping first 3 lines
for iline in range(nlines):
    line1 = flist.split('\n')[iline+3]
    line1 = line1.split(',')
    xx[iline] = np.array([float(line1[0].split("(")[1]), float(line1[2])], dtype='int')
    yy[iline] = np.array([float(line1[1]), float(line1[3].split(")")[0])], dtype='int')

Get trail position along the full spectral direction.

In [ ]:
win = 25
hwin = (win-1)//2
ntrails=2

trail = np.zeros((ntrails,ny))
for itrail in range(ntrails):
    pfit = np.poly1d(np.polyfit(yy[itrail,], xx[itrail,], 1))
    trail[itrail,] = pfit(np.arange(ny))

## Extract the spectra

Use the trails to extract the spectra from the science image (we will do an unweighted extraction).

In [ ]:
# Prepare arrays
spec = np.zeros((ntrails,ny))
sky = np.zeros((ntrails,ny))

# Extract the spectra
for itrail in range(ntrails):
    for iy in range(ny):
        xpos = int(trail[itrail,iy])
        sky_i = np.nanmedian(np.array([img[iy,xpos-win:xpos-hwin].flatten(), img[iy,xpos+hwin:xpos+win].flatten()]))
        spec_i = img[iy,xpos-hwin:xpos+hwin]
        sky[itrail,iy] = sky_i
        spec[itrail,iy] = (spec_i - sky_i).sum()

# Save extracted data
np.save('spec1.npy',spec[0,])
np.save('spec2.npy',spec[1,])
np.save('sky1.npy',sky[0,])
np.save('sky2.npy',sky[1,])

## Plot the extracted data

Try plotting the extracted spectra from the 2 sources and the extracted sky spectra. You have some example code commented out below to plot that, but try having a go yourself first. Take into account that we have not performed any wavelength calibration, so in the x-axis you will only have "pixels", and not "wavelength". Similarly with the flux, in the y-axis you will only have the number of counts observed, since we have not performed any flux calibration.

Once you have the plot, try to answer the following questions (question number 4 is simply the plot):

4. Plot the 1D extracted spectrum of the sources and the sky.

5. Look at the extracted sky spectra. Contrary to what we saw in the lecture, the sky emission lines are not clearly visible. The sky spectrum looks smooth and low-resolution. What does this tell you about the slit?

6. Look at the extracted spectrum of the two sources. Even without having performed any flux calibration, could you tell which one of the stars is hotter? Why?

7. Among the methods discussed for wavelength calibration, which one(s) would be applicable to these data?


In [ ]:
# # Example plots

# # Plot source
# fig, ax = plt.subplots(figsize=(10,6))
# ax.plot(spec[0,])
# ax.plot(spec[1,])
# ax.set_xlabel('Pixel along spectral direction')
# ax.set_ylabel('Total counts')
# ax.set_title('Source')
# plt.tight_layout()
# plt.savefig('spec.pdf')
# plt.show()

# # Plot sky
# fig, ax = plt.subplots(figsize=(10,6))
# ax.plot(sky[0,])
# ax.plot(sky[1,])
# ax.set_xlabel('Pixel along spectral direction')
# ax.set_ylabel('Total counts')
# ax.set_title('Sky')
# plt.tight_layout()
# plt.savefig('spec.pdf')
# plt.show()